In [2]:
# import libraries
import numpy as np
import random

In [188]:
# these are the possible moves
splits = [(0,1), (0,2), (1,3), (1,4), (2,5), (2,6), (3,4), (3,7),\
          (4,3), (4,5), (4,7), (5,4), (5,6), (5,8), (6,5), (6,8),\
          (7,3), (7,4), (7,9), (8,5), (8,6), (8,9)]

# adapt the reward structure to consider state of completion
completion_rate_list = [i/10.0 for i in range(0, 11)]

In [189]:
# create rewards look-up table
rtable = {}
for i in splits:
    for k in completion_rate_list:
        key = "{}, {}".format(i, k)
        rtable[key] = 1

In [190]:
# alter rewards as necessary in table
for i, j in rtable.iteritems():
    if '0, 1' in i:
        rtable[i] = 0.0
    elif '0, 2' in i:
        rtable[i] = 0.5
    elif '4, 5' in i or '5, 4' in i:
        rtable[i] = 2.0

for i, j in rtable.iteritems():
    if i=='(7, 9), 0.0': rtable[i] = 0.0
    elif i=='(7, 9), 0.1': rtable[i] = 0.0
    elif i=='(7, 9), 0.2': rtable[i] = 0.0
    elif i=='(7, 9), 0.3': rtable[i] = 0.0
    elif i=='(7, 9), 0.4': rtable[i] = 0.0
    elif i=='(7, 9), 0.5': rtable[i] = 0.0
    elif i=='(7, 9), 0.6': rtable[i] = 0.0
    elif i=='(7, 9), 0.7': rtable[i] = 0.0
    elif i=='(7, 9), 0.8': rtable[i] = 10.0
    elif i=='(7, 9), 0.9': rtable[i] = 10.0
        
for i, j in rtable.iteritems():
    if i=='(8, 9), 0.0': rtable[i] = 0.0
    elif i=='(8, 9), 0.1': rtable[i] = 0.0
    elif i=='(8, 9), 0.2': rtable[i] = 0.0
    elif i=='(8, 9), 0.3': rtable[i] = 0.0
    elif i=='(8, 9), 0.4': rtable[i] = 0.0
    elif i=='(8, 9), 0.5': rtable[i] = 0.0
    elif i=='(8, 9), 0.6': rtable[i] = 0.0
    elif i=='(8, 9), 0.7': rtable[i] = 0.0
    elif i=='(8, 9), 0.8': rtable[i] = 10.0
    elif i=='(8, 9), 0.9': rtable[i] = 10.0

In [191]:
mtable = {}
for i in splits:
    key = "{}".format(i)
    mtable[key] = 0

In [192]:
for i, j in mtable.iteritems():
    if '0, 1' in i or '3, 4' in i or '4, 3' in i or '5, 6' in i or '6, 5' in i or '7, 9' in i:
        mtable[i] = 0.50
    elif '1, 3' in i or '3, 7' in i or '7, 3' in i:
        mtable[i] = 0.25
    elif '4, 5' in i or '5, 4' in i:
        mtable[i] = 0.75
    elif '0, 2' in i or '8, 9' in i:
        mtable[i] = 1.0
    elif '1, 4' in i or '2, 5' in i or '4, 7' in i or '5, 8' in i or '7, 4' in i or '8, 6' in i:
        mtable[i] = 0.35
    elif '2, 6' in i or '6, 8' in i or '8, 5' in i:
        mtable[i] = 0.10

In [193]:
# create q look-up table
q = {}
for i in splits:
    for j in completion_rate_list:
        key = "{}, {}".format(i, j)
        q[key] = 0

In [90]:
def rewardiplier(pct_complete, miles):
    y = (pct_complete) + ((pct_complete-0.5)/(0-0.5)) * miles
    return y

In [91]:
def initial_move(current_state, action, next_state, total_miles):
    # total_miles = total_miles + m[0, start_action]
    update_q(current_state, action=start_action, next_state=start_action,\
             decision_miles=total_miles, alpha=alpha, gamma=gamma)
    current_state = next_state
    return (current_state, total_miles)

In [92]:
def update_q(current_state, action, next_state, decision_miles, alpha, gamma):
    pct_complete = round((decision_miles / target_miles),1)
    if pct_complete > 1.0:
        pct_complete = 1.0
    reward = r[current_state, action] * rewardiplier(pct_complete, m[current_state, action])
    k = str(str((current_state, next_state))+", "+str(target_miles)+", "+str(pct_complete))
    q_value = q[k]
    next_q_values = []
    for i in q.keys():
        if i[4] == str(next_state):
            next_q_values.append(q[i])
    new_q = q_value + alpha * (reward + gamma * max(next_q_values) - q_value)
    q[k] = new_q
    return r[current_state, action]

In [93]:
# define global parameters
target_miles = 6.0
gamma = 0.8
alpha = 1
epsilon = 0.3
n_actions = 10
final_destination = 9
random_state = np.random.RandomState(1999) 

In [35]:
# define state parameters
target_miles_list = np.arange(3.0,21.0)
completion_rate_list = [i/10.0 for i in range(0, 11)]
splits = [(0,1), (0,2), (1,3), (1,4), (2,5), (2,6), (3,4), (3,7),\
          (4,3), (4,5), (4,7), (5,4), (5,6), (5,8), (6,5), (6,8),\
          (7,3), (7,4), (7,9), (8,5), (8,6), (8,9), (9,9)]

In [36]:
# create q look-up table
q = {}
for i in splits:
    for j in target_miles_list:
        for k in completion_rate_list:
            key = "{}, {}, {}".format(i, j, k)
            q[key] = 0

In [14]:
q

{'(0, 1), 0.0': 0,
 '(0, 1), 0.1': 0,
 '(0, 1), 0.2': 0,
 '(0, 1), 0.3': 0,
 '(0, 1), 0.4': 0,
 '(0, 1), 0.5': 0,
 '(0, 1), 0.6': 0,
 '(0, 1), 0.7': 0,
 '(0, 1), 0.8': 0,
 '(0, 1), 0.9': 0,
 '(0, 2), 0.0': 0,
 '(0, 2), 0.1': 0,
 '(0, 2), 0.2': 0,
 '(0, 2), 0.3': 0,
 '(0, 2), 0.4': 0,
 '(0, 2), 0.5': 0,
 '(0, 2), 0.6': 0,
 '(0, 2), 0.7': 0,
 '(0, 2), 0.8': 0,
 '(0, 2), 0.9': 0,
 '(1, 3), 0.0': 0,
 '(1, 3), 0.1': 0,
 '(1, 3), 0.2': 0,
 '(1, 3), 0.3': 0,
 '(1, 3), 0.4': 0,
 '(1, 3), 0.5': 0,
 '(1, 3), 0.6': 0,
 '(1, 3), 0.7': 0,
 '(1, 3), 0.8': 0,
 '(1, 3), 0.9': 0,
 '(1, 4), 0.0': 0,
 '(1, 4), 0.1': 0,
 '(1, 4), 0.2': 0,
 '(1, 4), 0.3': 0,
 '(1, 4), 0.4': 0,
 '(1, 4), 0.5': 0,
 '(1, 4), 0.6': 0,
 '(1, 4), 0.7': 0,
 '(1, 4), 0.8': 0,
 '(1, 4), 0.9': 0,
 '(2, 5), 0.0': 0,
 '(2, 5), 0.1': 0,
 '(2, 5), 0.2': 0,
 '(2, 5), 0.3': 0,
 '(2, 5), 0.4': 0,
 '(2, 5), 0.5': 0,
 '(2, 5), 0.6': 0,
 '(2, 5), 0.7': 0,
 '(2, 5), 0.8': 0,
 '(2, 5), 0.9': 0,
 '(2, 6), 0.0': 0,
 '(2, 6), 0.1': 0,
 '(2, 6), 0.

In [103]:
for i in range(500):
    print "NEW RUN"
    start_action = random.choice([2]) # head to entrance a or b
    current_state, total_miles = initial_move(current_state=0,\
                            action=start_action, next_state=start_action, total_miles=0)
    print ("Initial state = ", current_state)
    goal = False
    while not goal:
        print "NEW SPLIT POINT"
        valid_moves = r[current_state] >= 0
        if total_miles > 0.75 * target_miles:
            print "High total miles."
            actions = np.array(list(range(n_actions)))
            actions = actions[valid_moves == True]
            if 9 in actions and m[current_state, final_destination] + total_miles > (0.99*target_miles):
                print("9 is here - going home")
                new_miles = m[current_state,final_destination]
                total_miles += new_miles
                next_state = final_destination
            else:
                shortest = min(list(m[current_state][actions]))
                print("taking shortest route")
                if total_miles > 20:
                    break
                new_miles = shortest
                total_miles += new_miles
                next_state = [i for i,x in enumerate(m[current_state]) if x == shortest][0]
        else:
            if random.random() < epsilon: 
                print "using random choice to pick next state"
                actions = np.array(list(range(n_actions)))
                actions = actions[valid_moves == True]
                random_state.shuffle(actions) 
                action = actions[0]
                new_miles = m[current_state,action]
                total_miles += new_miles
                next_state = action
            else:
                print "exploit"
                current_q_values = []
                for i in q.keys():
                    if i[3] == str(current_state):
                        current_q_values.append(q[i])
                if np.sum(current_q_values) > 0:
                    print "there is info to exploit"
                    current_q_values = []
                    for i in q.keys():
                        if i[3] == str(current_state):
                            current_q_values.append(q[i[4]])
                    action = np.argmax(current_q_values)
                    new_miles = m[current_state,action]
                    total_miles += new_miles
                else:
                    print "no info to exploit yet"
                    actions = np.array(list(range(n_actions)))
                    actions = actions[valid_moves == True]
                    random_state.shuffle(actions)
                    action = actions[0]
                    new_miles = m[current_state,action]
                    total_miles += new_miles
                next_state = action
        print("the current state = ", current_state)
        print("the next state = ", next_state)
        decision_miles = total_miles - new_miles
        reward = update_q(current_state, action, next_state, decision_miles, alpha, gamma)
        
        if next_state == 9:
            goal = True
        current_state = next_state   
        if type(current_state) == list:
            current_state = int(current_state[0])
        print("miles this far in this run = ", total_miles)
        print("----------")
    print("total miles - ", total_miles)

NEW RUN
('Initial state = ', 2)
NEW SPLIT POINT
using random choice to pick next state
('the current state = ', 2)
('the next state = ', 6)
('miles this far in this run = ', 0.10000000149011612)
----------
NEW SPLIT POINT
using random choice to pick next state
('the current state = ', 6)
('the next state = ', 5)
('miles this far in this run = ', 0.60000000149011612)
----------
NEW SPLIT POINT
using random choice to pick next state
('the current state = ', 5)
('the next state = ', 8)
('miles this far in this run = ', 0.94999999552965164)
----------
NEW SPLIT POINT
exploit
no info to exploit yet
('the current state = ', 8)
('the next state = ', 6)
('miles this far in this run = ', 1.2999999895691872)
----------
NEW SPLIT POINT
exploit
no info to exploit yet
('the current state = ', 6)
('the next state = ', 8)
('miles this far in this run = ', 1.3999999910593033)
----------
NEW SPLIT POINT
exploit
no info to exploit yet
('the current state = ', 8)
('the next state = ', 9)
('miles this far

In [22]:
# user inputs
target_miles = 6.0

# model parameters
gamma = 0.8
alpha = 1
epsilon = 0.3
n_actions = 10
final_destination = 9
random_state = np.random.RandomState(1999)

# learn!
for i in range(500):
    # start_action = random.choice([2]) # head to entrance a or b
#     current_state, total_miles = initial_move(current_state=0,\
#                             action=start_action, next_state=start_action, total_miles=0)
    
    current_state = 0
    
    current_total_miles = 0
    
    action = random.choice([2]) # head to entrance a or b
    
    pct_complete = round((current_total_miles / target_miles), 1)
        
    transition = "(" + str(current_state) + ", " + str(action) + "), " + str(pct_complete)
    
    reward = rtable[transition]
    
    qval = q[transition]
    
    next_qvals = [value for key, value in q.items() if key.lower()[1]==str(action)]
    
    new_qval = qval + alpha * (reward + gamma * max(next_qvals) - qvals)
    
    q[transition] = new_q
    
    addmiles = mtable["(" + str(current_state) + ", " + str(action) + ")"]
    
    current_total_miles += addmiles
    
    current_state = action
    
    goal = False
    
    while not goal:
        
        
        
        
        valid_moves = r[current_state] >= 0
        if total_miles > 0.75 * target_miles:
            print "High total miles."
            actions = np.array(list(range(n_actions)))
            actions = actions[valid_moves == True]
            if 9 in actions and m[current_state, final_destination] + total_miles > (0.99*target_miles):
                print("9 is here - going home")
                new_miles = m[current_state,final_destination]
                total_miles += new_miles
                next_state = final_destination
            else:
                shortest = min(list(m[current_state][actions]))
                print("taking shortest route")
                if total_miles > 20:
                    break
                new_miles = shortest
                total_miles += new_miles
                next_state = [i for i,x in enumerate(m[current_state]) if x == shortest][0]
        else:
            if random.random() < epsilon: 
                print "using random choice to pick next state"
                actions = np.array(list(range(n_actions)))
                actions = actions[valid_moves == True]
                random_state.shuffle(actions) 
                action = actions[0]
                new_miles = m[current_state,action]
                total_miles += new_miles
                next_state = action
            else:
                print "exploit"
                current_q_values = []
                for i in q.keys():
                    if i[3] == str(current_state):
                        current_q_values.append(q[i])
                if np.sum(current_q_values) > 0:
                    print "there is info to exploit"
                    current_q_values = []
                    for i in q.keys():
                        if i[3] == str(current_state):
                            current_q_values.append(q[i[4]])
                    action = np.argmax(current_q_values)
                    new_miles = m[current_state,action]
                    total_miles += new_miles
                else:
                    print "no info to exploit yet"
                    actions = np.array(list(range(n_actions)))
                    actions = actions[valid_moves == True]
                    random_state.shuffle(actions)
                    action = actions[0]
                    new_miles = m[current_state,action]
                    total_miles += new_miles
                next_state = action
        print("the current state = ", current_state)
        print("the next state = ", next_state)
        decision_miles = total_miles - new_miles
        reward = update_q(current_state, action, next_state, decision_miles, alpha, gamma)
        
        if next_state == 9:
            goal = True
        current_state = next_state   
        if type(current_state) == list:
            current_state = int(current_state[0])
        print("miles this far in this run = ", total_miles)
        print("----------")
    print("total miles - ", total_miles)

NameError: name 'initial_move' is not defined

In [82]:
print "Start Parameters:"
gamma = 0.8
alpha = 1
epsilon = 0.3
random_state = np.random.RandomState(1999)

print "gamma: {}, alpha: {}, epsilon: {}".format(gamma, alpha, epsilon)

current_state = 0
print "current state: {}".format(current_state)

current_total_miles = 0
print "current miles: {}".format(current_total_miles)

action = random.choice([2]) # head to entrance a or b
print "start action: {}".format(action)

pct_complete = round((current_total_miles / target_miles), 1)
print "completed: {}".format(pct_complete)

transition = "(" + str(current_state) + ", " + str(action) + "), " + str(pct_complete)
print "transition state: {}".format(transition)

reward = rtable[transition]
print "reward: {}".format(reward)

qval = q[transition]
print "q value of this transition: {}".format(qval)

next_qvals = [value for key, value in q.items() if key.lower()[1]==str(action)]
print "possible q values from future move: {}".format(next_qvals)

new_qval = qval + alpha * (reward + gamma * max(next_qvals) - qval)
print "updated q value: {}".format(new_qval)

q[transition] = new_qval

addmiles = mtable["(" + str(current_state) + ", " + str(action) + ")"]
print "miles to add: {}".format(addmiles)

current_total_miles += addmiles
print "total miles after initial move: {}".format(current_total_miles)

current_state = action
print "current start after initial move: {}".format(current_state)

valid_moves = [key for key, value in mtable.items() if key.lower()[1]==str(current_state)]
print "valid next moves: {}".format(valid_moves)

action = random.choice(valid_moves)
print "action you are taking randomly: {}".format(action[4])

transition = action + ", " + str(pct_complete)
print "transition state from random action: {}".format(transition)

reward = rtable[transition]
print "reward from random pick: {}".format(reward)

qval = q[transition]
print "q value of this transition: {}".format(qval)

# add miles
addmiles = mtable[action]
print "miles to add: {}".format(addmiles)

current_total_miles += addmiles
print "total miles after this move: {}".format(current_total_miles)

pct_complete = round((current_total_miles / target_miles), 1)
print "completed: {}".format(pct_complete)

# update q
next_qvals = [value for key, value in q.items() if key.lower()[1]==str(action[4])]
print "possible q values from future move: {}".format(next_qvals)

new_qval = qval + alpha * (reward + gamma * max(next_qvals) - qval)
print "updated q value: {}".format(new_qval)

q[transition] = new_qval

current_state = action[4]
print "current start after this move: {}".format(current_state)

valid_moves = [key for key, value in mtable.items() if key.lower()[1]==str(current_state)]
print "valid next moves: {}".format(valid_moves)

# for current state, what are the q values you know about next potential moves
print pct_complete

exploit_vals = [value for key, value in q.items() if key.lower()[1]==str(current_state) and key[8:11]==str(pct_complete)]
exploit_keys = [key for key, value in q.items() if key.lower()[1]==str(current_state) and key[8:11]==str(pct_complete)]

print exploit_vals
print exploit_keys

action = exploit_keys[exploit_vals.index(max(exploit_vals))][4]




Start Parameters:
gamma: 0.8, alpha: 1, epsilon: 0.3
current state: 0
current miles: 0
start action: 2
completed: 0.0
transition state: (0, 2), 0.0
reward: 0.5
q value of this transition: 1.3
possible q values from future move: [0, 0, 0, 0, 0, 0, 1.0, 0, 0, 0, 0, 1.0, 0, 0, 0, 0, 0, 0, 0, 0]
updated q value: 1.3
miles to add: 1.0
total miles after initial move: 1.0
current start after initial move: 2
valid next moves: ['(2, 6)', '(2, 5)']
action you are taking randomly: 6
transition state from random action: (2, 6), 0.0
reward from random pick: 1
q value of this transition: 1.0
miles to add: 0.1
total miles after this move: 1.1
completed: 0.2
possible q values from future move: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
updated q value: 1.0
current start after this move: 6
valid next moves: ['(6, 5)', '(6, 8)']
0.2
[2, 0]
['(6, 8), 0.2', '(6, 5), 0.2']


In [88]:
# starting metrics
# gamma, alpha, epsilon
# current state = 0
# target miles and total miles (starts at 0)
# set random state for replication


# define current state (current_state)
# calculate percent of run complete (pct_complete)
# define next possible states (valid_moves)
# determine to exploit of not (epsilon > x)
# define action (action & transition)
# determine reward (reward)
# update q value (new_qvals)
# increment mileage (addmiles)
# set current state to previous action

'8'

In [186]:
# create q look-up table
q = {}
for i in splits:
    for j in completion_rate_list:
        key = "{}, {}".format(i, j)
        q[key] = 0

In [ ]:
for i in range(100):
    # starting metrics
    # gamma, alpha, epsilon
    gamma = 0.8; alpha = 1; epsilon = 0.3
    # current state = 0
    current_state = 0
    # target miles and total miles (starts at 0)
    target_miles = 5; current_total_miles = 0
    # set random state for replication
    random_state = np.random.RandomState(1999)
    # set goal to False
    goal = False

    while not goal:

        # calculate percent of run complete (pct_complete)
        pct_complete = round((current_total_miles / target_miles), 1)
        print "completed: {}".format(pct_complete)

        # define next possible states (valid_moves)
        valid_moves = [key for key, value in mtable.items() if key.lower()[1]==str(current_state)]
        print "valid next moves: {}".format(valid_moves)

        # determine to exploit of not (epsilon > random number). Exploit or explore.
        if random.random() < epsilon:

        # if not exploiting...
            print "not exploiting"

        # define action (action)
            action = random.choice(valid_moves)
            print "action you are taking randomly: {}".format(action[4])

        # if exploiting

        else:

            print "exploiting"

        # define action (action & transition)
            exploit_vals = [value for key, value in q.items() if key.lower()[1]==str(current_state) and key[8:11]==str(pct_complete)]

            exploit_keys = [key for key, value in q.items() if key.lower()[1]==str(current_state) and key[8:11]==str(pct_complete)]

            action = exploit_keys[exploit_vals.index(max(exploit_vals))][:6]
            print "action you are taking exploitingly: {}".format(action[4])

        if action[4] == '9':
            break

        # define transition
        transition = action + ", " + str(pct_complete)
        print "transition state from random action: {}".format(transition)

        # determine reward (reward)
        reward = rtable[transition]
        print "reward: {}".format(reward)

        # update q value (new_qvals)
        # update q
        next_qvals = [value for key, value in q.items() if key.lower()[1]==str(action[4])]
        print "possible q values from future move: {}".format(next_qvals)

        new_qval = qval + alpha * (reward + gamma * max(next_qvals) - qval)
        print "updated q value: {}".format(new_qval)

        q[transition] = new_qval

        # increment mileage (addmiles)
        # add miles
        current_total_miles += mtable[action]
        print "total miles after move: {}".format(current_total_miles)

        # set current state to previous action
        current_state = action[4]

        if current_total_miles >= target_miles or current_state == 9:
            goal = True

    print "Run Complete"
    print "Total Miles: {}".format(current_total_miles)

completed: 0.0
valid next moves: ['(0, 1)', '(0, 2)']
exploiting
action you are taking exploitingly: 2
action you are taking exploitingly: <type 'str'>
transition state from random action: (0, 2), 0.0
reward: 0.5
possible q values from future move: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
updated q value: 0.5
total miles after move: 1.0
completed: 0.2
valid next moves: ['(2, 6)', '(2, 5)']
exploiting
action you are taking exploitingly: 6
action you are taking exploitingly: <type 'str'>
transition state from random action: (2, 6), 0.2
reward: 1
possible q values from future move: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
updated q value: 1.0
total miles after move: 1.1
completed: 0.2
valid next moves: ['(6, 5)', '(6, 8)']
exploiting
action you are taking exploitingly: 8
action you are taking exploitingly: <type 'str'>
transition state from random action: (6, 8), 0.2
reward: 1
possible q values from future move: [0, 0, 0, 0, 0, 0, 0, 0, 

In [165]:
current_state = action[4]

In [166]:
current_state

'6'

In [195]:
q

{'(0, 1), 0.0': 7.1999999999999975,
 '(0, 1), 0.1': 0,
 '(0, 1), 0.2': 0,
 '(0, 1), 0.3': 0,
 '(0, 1), 0.4': 0,
 '(0, 1), 0.5': 0,
 '(0, 1), 0.6': 0,
 '(0, 1), 0.7': 0,
 '(0, 1), 0.8': 0,
 '(0, 1), 0.9': 0,
 '(0, 1), 1.0': 0,
 '(0, 2), 0.0': 7.6999999999999975,
 '(0, 2), 0.1': 0,
 '(0, 2), 0.2': 0,
 '(0, 2), 0.3': 0,
 '(0, 2), 0.4': 0,
 '(0, 2), 0.5': 0,
 '(0, 2), 0.6': 0,
 '(0, 2), 0.7': 0,
 '(0, 2), 0.8': 0,
 '(0, 2), 0.9': 0,
 '(0, 2), 1.0': 0,
 '(1, 3), 0.0': 0,
 '(1, 3), 0.1': 8.199999999999998,
 '(1, 3), 0.2': 0,
 '(1, 3), 0.3': 0,
 '(1, 3), 0.4': 0,
 '(1, 3), 0.5': 0,
 '(1, 3), 0.6': 0,
 '(1, 3), 0.7': 0,
 '(1, 3), 0.8': 0,
 '(1, 3), 0.9': 0,
 '(1, 3), 1.0': 0,
 '(1, 4), 0.0': 0,
 '(1, 4), 0.1': 8.999999999999996,
 '(1, 4), 0.2': 0,
 '(1, 4), 0.3': 0,
 '(1, 4), 0.4': 0,
 '(1, 4), 0.5': 0,
 '(1, 4), 0.6': 0,
 '(1, 4), 0.7': 0,
 '(1, 4), 0.8': 0,
 '(1, 4), 0.9': 0,
 '(1, 4), 1.0': 0,
 '(2, 5), 0.0': 0,
 '(2, 5), 0.1': 0,
 '(2, 5), 0.2': 8.999999999999996,
 '(2, 5), 0.3': 0,
 '(2, 

In [ ]:
%matplotlib inline
plt.plot(miles, complete, 'ro')
plt.show()